In [1]:
import numpy as np
import tensorflow as tf
import sionna.rt as rt
import sionna.channel as ch
import matplotlib.pyplot as plt

2024-11-21 15:46:06.139419: E external/local_xla/xla/stream_executor/cuda/cuda_dnn.cc:9261] Unable to register cuDNN factory: Attempting to register factory for plugin cuDNN when one has already been registered
2024-11-21 15:46:06.139455: E external/local_xla/xla/stream_executor/cuda/cuda_fft.cc:607] Unable to register cuFFT factory: Attempting to register factory for plugin cuFFT when one has already been registered
2024-11-21 15:46:06.140460: E external/local_xla/xla/stream_executor/cuda/cuda_blas.cc:1515] Unable to register cuBLAS factory: Attempting to register factory for plugin cuBLAS when one has already been registered
2024-11-21 15:46:06.146200: I tensorflow/core/platform/cpu_feature_guard.cc:182] This TensorFlow binary is optimized to use available CPU instructions in performance-critical operations.
To enable the following instructions: AVX2 FMA, in other operations, rebuild TensorFlow with the appropriate compiler flags.
2024-11-21 15:46:06.690374: W tensorflow/compiler/tf2

In [2]:
scene = rt.load_scene("../Assets/NCSA_Room_Scan_Translated/NCSAConferenceRoom.xml")
scene.frequency = 5.33e9

2024-11-21 15:46:08.596834: I external/local_xla/xla/stream_executor/cuda/cuda_executor.cc:901] successful NUMA node read from SysFS had negative value (-1), but there must be at least one NUMA node, so returning NUMA node zero. See more at https://github.com/torvalds/linux/blob/v6.0/Documentation/ABI/testing/sysfs-bus-pci#L344-L355
2024-11-21 15:46:08.597060: I external/local_xla/xla/stream_executor/cuda/cuda_executor.cc:901] successful NUMA node read from SysFS had negative value (-1), but there must be at least one NUMA node, so returning NUMA node zero. See more at https://github.com/torvalds/linux/blob/v6.0/Documentation/ABI/testing/sysfs-bus-pci#L344-L355
2024-11-21 15:46:08.597225: I external/local_xla/xla/stream_executor/cuda/cuda_executor.cc:901] successful NUMA node read from SysFS had negative value (-1), but there must be at least one NUMA node, so returning NUMA node zero. See more at https://github.com/torvalds/linux/blob/v6.0/Documentation/ABI/testing/sysfs-bus-pci#L344-

In [9]:
scene.objects['facric_obj'].radio_material = "itu_wood"
scene.objects['glass_tv_obj'].radio_material = "itu_glass"
scene.objects['metal_obj'].radio_material = "itu_metal"
scene.objects['plastic_obj'].radio_material = "itu_plasterboard"
scene.objects['walls_obj'].radio_material = "itu_plasterboard"
scene.objects['whiteboards_obj'].radio_material = "itu_metal"
scene.objects['wood_obj'].radio_material = "itu_wood"

In [3]:
scene.tx_array = rt.AntennaArray(antenna = rt.Antenna("iso", "V"), positions=[0,0,0])

In [4]:
scene.rx_array = rt.AntennaArray(antenna = rt.Antenna("iso", "V"), positions=[0,0,0])

In [5]:
tx_x = 2
tx_y = 1
tx_z = 2

tx = rt.Transmitter(name = "tx", 
                        position=tf.Variable([tx_x, tx_y, tx_z], dtype=tf.float32),
                        orientation=tf.Variable([0, 0, 0], dtype=tf.float32),
                        power_dbm=tf.Variable(25.0, dtype=tf.float32))
scene.add(tx)

In [6]:
rx_x = 0
rx_y = 1
rx_z = 2
rx = rt.Receiver(name = "rx", 
                        position=tf.Variable([rx_x, rx_y, rx_z], dtype=tf.float32),
                        orientation=tf.Variable([0, 0, 0], dtype=tf.float32))
scene.add(rx)

In [61]:
ps = scene.compute_paths(max_depth = 1, 
                         method='exhaustive', 
                         num_samples = 1e6, 
                         reflection = True,
                         diffraction = False,
                         scattering = False,
                         los = True)

In [62]:
scene.preview(show_devices = True, 
              show_paths = True, paths = ps, 
              coverage_map = None,
              clip_at = 2,
              clip_plane_orientation=(0, -0.5, -1))

Renderer(camera=PerspectiveCamera(aspect=1.31, children=(DirectionalLight(intensity=0.25, matrixWorldNeedsUpda…

In [63]:
a, tau = ps.cir()

In [60]:
a_old = a
t_old = tau


In [70]:
np.array(tau).reshape((6,))[1:] - np.array(tau).reshape((6,))[1]

array([0.0000000e+00, 1.4902504e-08, 2.4594389e-09, 2.6977837e-08,
       2.9723608e-08], dtype=float32)

In [65]:
t_old

<tf.Tensor: shape=(1, 1, 1, 5), dtype=float32, numpy=
array([[[[0.0000000e+00, 1.4902504e-08, 2.4594389e-09, 2.6977837e-08,
          2.9723608e-08]]]], dtype=float32)>

In [17]:
freqs = ch.subcarrier_frequencies(15,312000)
h_matrix = ch.cir_to_ofdm_channel(freqs,a,tau,normalize=False)

In [18]:
h_matrix

<tf.Tensor: shape=(1, 1, 1, 1, 1, 1, 15), dtype=complex64, numpy=
array([[[[[[[8.952225e-08+0.j, 8.952225e-08+0.j, 8.952225e-08+0.j,
             8.952225e-08+0.j, 8.952225e-08+0.j, 8.952225e-08+0.j,
             8.952225e-08+0.j, 8.952225e-08+0.j, 8.952225e-08+0.j,
             8.952225e-08+0.j, 8.952225e-08+0.j, 8.952225e-08+0.j,
             8.952225e-08+0.j, 8.952225e-08+0.j, 8.952225e-08+0.j]]]]]]],
      dtype=complex64)>

In [11]:
np.array(h_matrix).imag

array([[[[[[[0., 0., 0., 0., 0., 0., 0., 0., 0., 0., 0., 0., 0., 0.,
             0.]]]]]]], dtype=float32)

In [31]:
tau

<tf.Tensor: shape=(1, 1, 1, 5), dtype=float32, numpy=
array([[[[0.0000000e+00, 1.4902504e-08, 2.4594389e-09, 2.6977837e-08,
          2.9723608e-08]]]], dtype=float32)>

In [15]:
a

<tf.Tensor: shape=(1, 1, 1, 1, 1, 1, 1), dtype=complex64, numpy=array([[[[[[[0.00223797+0.j]]]]]]], dtype=complex64)>